# Improving classification datasets

In [1]:
from ekorpkit import eKonf

eKonf.setLogger("INFO")
print("version:", eKonf.__version__)

is_colab = eKonf.is_colab()
print("is colab?", is_colab)
if is_colab:
    eKonf.mount_google_drive()
workspace_dir = "/workspace"
project_name = "ekorpkit-book/exmaples/esg"
ws = eKonf.set_workspace(workspace=workspace_dir, project=project_name)
print("project_dir:", ws.project_dir)
ws.envs.dict()

INFO:ekorpkit.utils.notebook:Google Colab not detected.
INFO:ekorpkit.base:Set environment variable EKORPKIT_PROJECT=ekorpkit-book/exmaples/esg
INFO:ekorpkit.base:Set environment variable EKORPKIT_PROJECT_DIR=/workspace/projects/ekorpkit-book/exmaples/esg


version: 0.1.40.post0.dev50
is colab? False


INFO:root:compose config with overrides: ['project=default']
INFO:ekorpkit.base:There are no arguments to initilize a config, using default config.


project_dir: /workspace/projects/ekorpkit-book/exmaples/esg


{'EKORPKIT_CONFIG_DIR': '/workspace/projects/ekorpkit-book/config',
 'EKORPKIT_WORKSPACE_ROOT': '/workspace',
 'EKORPKIT_PROJECT': 'ekorpkit-book/exmaples/esg',
 'EKORPKIT_PROJECT_DIR': '/workspace/projects/ekorpkit-book/exmaples/esg',
 'EKORPKIT_DATA_DIR': None,
 'EKORPKIT_LOG_LEVEL': 'INFO',
 'NUM_WORKERS': 230,
 'KMP_DUPLICATE_LIB_OK': 'TRUE',
 'CUDA_DEVICE_ORDER': None,
 'CUDA_VISIBLE_DEVICES': None,
 'WANDB_PROJECT': None,
 'WANDB_DISABLED': None,
 'LABEL_STUDIO_SERVER': 'http://ekorpkit-labelstudio:8080',
 'CACHED_PATH_CACHE_ROOT': None}

time: 1.1 s (started: 2022-12-12 10:24:03 +00:00)


## Preparing `esg_topics` dataset

In [2]:
ds_cfg = eKonf.compose('dataset')
ds_cfg.name = 'esg_topics'
ds_cfg.data_dir = '/workspace/data/datasets/simple'
eKonf.print(ds_cfg)
# ds = eKonf.instantiate(ds_cfg)
# labels = list(ds.splits['train'].labels.unique())
# print(labels)

INFO:root:compose config with overrides: ['dataset=default']


{'_target_': 'ekorpkit.datasets.dataset.Dataset',
 'auto': {'build': False, 'load': True},
 'column_info': {'_target_': 'ekorpkit.info.column.DatasetInfo',
                 'columns': {'id': 'id', 'text': 'text'},
                 'data': {'id': 'int', 'text': 'str'},
                 'datetime': {'columns': None,
                              'format': None,
                              'rcParams': None}},
 'data_dir': '/workspace/data/datasets/simple',
 'filetype': '.parquet',
 'force': {'build': False},
 'info': {'_target_': 'ekorpkit.info.stat.SummaryInfo',
          'aggregate_info': {'num_examples': 'num_examples',
                             'size_in_bytes': 'num_bytes'},
          'data_dir': '/workspace/data/datasets/simple',
          'info_file': 'info-esg_topics.yaml',
          'info_list': ['name',
                        'fullname',
                        'domain',
                        'task',
                        'lang',
                        'description',
 

In [27]:
remap_cat = {
    'E-신재생에너지 발전': 'E-환경혁신',
    'E-원자력발전': 'E-환경혁신',
    'S-기술혁신': 'S-소비자',
    'S-노조/노사': 'S-고용',
    'S-인적자본': 'S-고용',
    'S-산업재해/안전관리': 'S-재해/안전관리',
    'G-정보공시': 'NA',
    'G-주주환원': 'NA',
}
remap_cat

{'E-신재생에너지 발전': 'E-환경혁신',
 'E-원자력발전': 'E-환경혁신',
 'S-기술혁신': 'S-소비자',
 'S-노조/노사': 'S-고용',
 'S-인적자본': 'S-고용',
 'S-산업재해/안전관리': 'S-재해/안전관리',
 'G-정보공시': 'NA',
 'G-주주환원': 'NA'}

In [28]:
for split, data in ds._splits.items():
    data['labels'] = data['labels'].map(remap_cat).fillna(data['labels'])
    data = data[data.labels != 'NA']
    ds._splits[split] = data

In [29]:
ds.save_as("esg_topics_remapped")

INFO:ekorpkit.base:Using batcher with minibatch size: 39


apply len_bytes to num_bytes:   0%|          | 0/230 [00:00<?, ?it/s]

INFO:ekorpkit.base:Using batcher with minibatch size: 5


apply len_bytes to num_bytes:   0%|          | 0/222 [00:00<?, ?it/s]

INFO:ekorpkit.base:Using batcher with minibatch size: 5


apply len_bytes to num_bytes:   0%|          | 0/199 [00:00<?, ?it/s]

In [30]:
ds_cfg.name = "esg_topics_remapped"
ds = eKonf.instantiate(ds_cfg)
labels = list(ds.splits['train'].labels.unique())
print(labels)

['S-기업(공급망)동반성장/상생', 'G-지배구조', 'G-기업윤리/불공정/소송', 'S-소비자', 'E-환경혁신', 'S-사회공헌', 'S-고용', 'E-환경영향', 'E-기후변화', 'S-재해/안전관리']


## Cross validation of `esg_topics` dataset

In [9]:
overrides=[
    '+model/transformer=classification',
    '+model/transformer/pretrained=ekonelectra-base',
]
model_cfg = eKonf.compose('model/transformer=classification', overrides)
model_cfg.name = "esg_topics"
model_cfg.dataset = ds_cfg
model_cfg.verbose = False
model_cfg.config.num_train_epochs = 2
model_cfg.config.max_seq_length = 256
model_cfg.config.train_batch_size = 32
model_cfg.config.eval_batch_size = 32
model_cfg._method_ = []
# model_cfg.model.eval.visualize.plot.confusion_matrix.include_values = False
# model_cfg.model.eval.visualize.plot.confusion_matrix.include_percentages = False
# model_cfg.model.eval.visualize.plot.figure.figsize = (12,10)
model = eKonf.instantiate(model_cfg)

INFO:ekorpkit.base:No method defined to call


In [8]:
cv_preds = model.cross_val_predict(cv=5)
eKonf.save_data(cv_preds, "esg_topics_cv_preds.parquet", data_dir)

Some weights of the model checkpoint at entelecheia/ekonelectra-base-discriminator were not used when initializing ElectraForSequenceClassification: ['discriminator_predictions.dense_prediction.weight', 'discriminator_predictions.dense_prediction.bias', 'discriminator_predictions.dense.bias', 'discriminator_predictions.dense.weight']
- This IS expected if you are initializing ElectraForSequenceClassification from the checkpoint of a model trained on another task or with another architecture (e.g. initializing a BertForSequenceClassification model from a BertForPreTraining model).
- This IS NOT expected if you are initializing ElectraForSequenceClassification from the checkpoint of a model that you expect to be exactly identical (initializing a BertForSequenceClassification model from a BertForSequenceClassification model).
Some weights of ElectraForSequenceClassification were not initialized from the model checkpoint at entelecheia/ekonelectra-base-discriminator and are newly initializ

  0%|          | 0/7074 [00:00<?, ?it/s]

Token indices sequence length is longer than the specified maximum sequence length for this model (533 > 512). Running this sequence through the model will result in indexing errors


Epoch:   0%|          | 0/2 [00:00<?, ?it/s]

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


...

  0%|          | 0/2210 [00:00<?, ?it/s]

Running Evaluation:   0%|          | 0/71 [00:00<?, ?it/s]

huggingface/tokenizers: The current process just got forked, after parallelism has already been used. Disabling parallelism to avoid deadlocks...
To disable this warning, you can either:
	- Avoid using `tokenizers` before the fork if possible
	- Explicitly set the environment variable TOKENIZERS_PARALLELISM=(true | false)


  0%|          | 0/2210 [00:00<?, ?it/s]

  0%|          | 0/71 [00:00<?, ?it/s]

## Use rubrix to find potential label errors

In [5]:
rb_cfg = eKonf.compose('model/rubrix')
rb_cfg.auto.init = True
rb = eKonf.instantiate(rb_cfg)


INFO:ekorpkit.base:Loaded .env from /workspace/projects/ekorpkit-book/config/.env
INFO:ekorpkit.base:Loaded .env from /workspace/projects/ekorpkit-book/config/.env
INFO:ekorpkit.base:Loaded .env from /workspace/projects/ekorpkit-book/config/.env


In [6]:
rb.get_workspace()

'esgml'

In [8]:
cv_preds = eKonf.load_data("esg_topics_cv_preds.parquet", data_dir)

In [9]:
records = rb.create_records_from_cv_preds(
    cv_preds,
)
records[0]

TextClassificationRecord(text='os 전쟁 구글 , 애플 , ms , 인텔 삼성전자 등 각각 의 iot 전용 os 강화\n업체 들 안드로이드 os 견제 해 아직 채택 안함 센서 고성장 전망 mems ( 반도체 센서 ) 시장 고성장 예상\n다만 , 국내 기술 은 매우 미흡\n인공지능 이 인공지능 이 3 세대 세대 deepdeep learninglearning 의 초기 초기 국면 으로 국면 으로 들어가면서들어가면서 혁신 이 혁신 이 일어나기일어나기 시작 인공지능 연구 가 3 세대 deep learning 의 초기 국면 으로 들어가면서 혁신 이 일어나기 시작 함', inputs={'text': 'os 전쟁 구글 , 애플 , ms , 인텔 삼성전자 등 각각 의 iot 전용 os 강화\n업체 들 안드로이드 os 견제 해 아직 채택 안함 센서 고성장 전망 mems ( 반도체 센서 ) 시장 고성장 예상\n다만 , 국내 기술 은 매우 미흡\n인공지능 이 인공지능 이 3 세대 세대 deepdeep learninglearning 의 초기 초기 국면 으로 국면 으로 들어가면서들어가면서 혁신 이 혁신 이 일어나기일어나기 시작 인공지능 연구 가 3 세대 deep learning 의 초기 국면 으로 들어가면서 혁신 이 일어나기 시작 함'}, prediction=[('E-기후변화', 0.0031880621893694222), ('E-환경영향', 0.005058959626738143), ('E-환경혁신', 0.010744794691714028), ('G-기업윤리/불공정/소송', 0.01250313787700796), ('G-지배구조', 0.018917387394747708), ('S-고용', 0.00931412617366345), ('S-기업(공급망)동반성장/상생', 0.0068541975270435635), ('S-사회공헌', 0.0037565036432219917), ('S-소비자', 0.9259529941013552), ('S-재해/안전관리', 0.003709

In [10]:
# get records with potential label errors
records_with_label_error = rb.find_label_errors(records)
records_with_label_error[0]

TextClassificationRecord(text='최근 이동통신 시장 은 lte 서비스 도입 으로 큰 변화 를 맞고 있음\nlte 는 3 g 이동통신망 으로 널리 채택 된 wcdma 방식 에서 발전 된 규격 으로 전세계 이동통신사 의 80 % 이상 이 lte 를 채택 하고 있음\n와이브로 는 한국 이 lte 와 경쟁 하고자 만든 차세대 국책사업 중 하나였지만 , 초기 시장 창출 실패 와 이동통신사업자 들 의 견제 , 정부 의 정책 부재 등으로 사업화 에 난항\n국내 lte 서비스 는 상용화 1 년 만에 1 , 000 만명을 넘어선 반면 , 와이브로 는 6 년이 지난 현재 까지도 사용자 가 100 만명 수준 에 불과한 실정\n이러한 통신시장 의 구조적 인 변화 는 와이브로 에 편중 된 동사 에 위기 로 작용 할 수 있음', inputs={'text': '최근 이동통신 시장 은 lte 서비스 도입 으로 큰 변화 를 맞고 있음\nlte 는 3 g 이동통신망 으로 널리 채택 된 wcdma 방식 에서 발전 된 규격 으로 전세계 이동통신사 의 80 % 이상 이 lte 를 채택 하고 있음\n와이브로 는 한국 이 lte 와 경쟁 하고자 만든 차세대 국책사업 중 하나였지만 , 초기 시장 창출 실패 와 이동통신사업자 들 의 견제 , 정부 의 정책 부재 등으로 사업화 에 난항\n국내 lte 서비스 는 상용화 1 년 만에 1 , 000 만명을 넘어선 반면 , 와이브로 는 6 년이 지난 현재 까지도 사용자 가 100 만명 수준 에 불과한 실정\n이러한 통신시장 의 구조적 인 변화 는 와이브로 에 편중 된 동사 에 위기 로 작용 할 수 있음'}, prediction=[('E-기후변화', 0.0030561790387218834), ('E-환경영향', 0.004940841001211258), ('E-환경혁신', 0.011977991797623686), ('G-기업윤리/불공정/소송', 0.00884969377797024), ('G-지배구조', 0.011248100661326789), 

In [11]:
len(records_with_label_error)

1408

In [12]:
# uncover label errors in the Rubrix web app
rb.log(records_with_label_error, "esg_topic_label_errors")

  0%|          | 0/1408 [00:00<?, ?it/s]

1408 records logged to http://ekorpkit-book:6900/datasets/esgml/esg_topic_label_errors


## Saving the re-labelled dataset

In [23]:
relabelled_dataset = rb.load("esg_topic_label_errors")

In [24]:
for split, data in ds._splits.items():
    data = rb.update_label_errors(data, relabelled_dataset, split=split)
    ds._splits[split] = data

In [25]:
len(ds.data[ds.data.labels != ds.data.original_labels])

27

In [32]:
ds.save_as("esg_topics_improved")
ds_cfg.name = "esg_topics_improved"
ds = eKonf.instantiate(ds_cfg)
labels = list(ds.splits['train'].labels.unique())
print(labels)

INFO:ekorpkit.base:Using batcher with minibatch size: 39


apply len_bytes to num_bytes:   0%|          | 0/230 [00:00<?, ?it/s]

INFO:ekorpkit.base:Using batcher with minibatch size: 5


apply len_bytes to num_bytes:   0%|          | 0/199 [00:00<?, ?it/s]

INFO:ekorpkit.base:Using batcher with minibatch size: 5


apply len_bytes to num_bytes:   0%|          | 0/222 [00:00<?, ?it/s]

['S-기업(공급망)동반성장/상생', 'G-지배구조', 'G-기업윤리/불공정/소송', 'S-소비자', 'E-환경혁신', 'S-사회공헌', 'S-고용', 'E-환경영향', 'E-기후변화', 'S-재해/안전관리']


In [33]:
ds.data_dir

'/workspace/data/datasets/simple/esg_topics_improved'